In [1]:
import json
from glob import glob
from tqdm import tqdm
import os
import shutil

In [4]:
!ls macaw-multimodal/synthetic-*images*.jsonl

macaw-multimodal/synthetic-multi-images-multi-audio-relationship.jsonl
macaw-multimodal/synthetic-multi-images-relationship.jsonl


In [5]:
files = glob('macaw-multimodal/synthetic-*images*.jsonl')
files

['macaw-multimodal/synthetic-multi-images-relationship.jsonl',
 'macaw-multimodal/synthetic-multi-images-multi-audio-relationship.jsonl']

In [6]:
!mkdir filtered-blip-images

In [9]:
images = []

for f in files:
    with open(f) as fopen:
        for l in tqdm(fopen):
            l = json.loads(l)
            for f_ in l['filename']:
                if f_.endswith('.jpg'):
                    images.append(f_)
#             break
#             img = l['image']
#             f_img = f'train2014/COCO_train2014_{img}'
#             if not os.path.exists(f_img):
#                 continue
#             shutil.copyfile(f_img, os.path.join('filtered-llava-images', img))

100000it [00:01, 88185.31it/s]
59400it [00:01, 52003.73it/s]


In [10]:
len(images)

259400

In [18]:
for img in tqdm(list(set(images))):
    f = os.path.join('blip', img)
    folder = f.split('/')[1]
    os.makedirs(os.path.join('filtered-blip-images', folder), exist_ok = True)
    shutil.copyfile(f, os.path.join('filtered-blip-images', img))

100%|██████████| 238135/238135 [17:04<00:00, 232.47it/s] 


In [19]:
!du -hs filtered-blip-images

12G	filtered-blip-images


In [20]:
!~/7zz -v5g a filtered-blip-images.7z filtered-blip-images > /dev/null

In [21]:
from huggingface_hub import HfApi
api = HfApi()

In [23]:
for f in glob('*.7z.*'):
    print(f)
    api.upload_file(
        path_or_fileobj=f,
        path_in_repo=f,
        repo_id='mesolitica/translated-LLaVA-Pretrain',
        repo_type='dataset',
)

filtered-blip-images.7z.003


filtered-blip-images.7z.003:   0%|          | 0.00/747M [00:00<?, ?B/s]

filtered-blip-images.7z.001


filtered-blip-images.7z.001:   0%|          | 0.00/5.37G [00:00<?, ?B/s]

filtered-blip-images.7z.002


filtered-blip-images.7z.002:   0%|          | 0.00/5.37G [00:00<?, ?B/s]

In [24]:
!rm *.7z.*

In [25]:
!du -hs blip

27G	blip
